In [181]:
import pandas as pd
from sklearn.cluster import DBSCAN
from sklearn.metrics.pairwise import haversine_distances
from math import radians
import folium
from sklearn.cluster import KMeans
from sklearn.cluster import AgglomerativeClustering
import numpy as np

Carrega o dataset

In [182]:
data = pd.read_csv("Cluster-Crime-Maio.csv")
data

ID  FONTE FLAGRANTE NATUREZA DA OCORRÊNCIA  \
0      1  CIOPS       NÃO         MORTE - A BALA   
1      2  CIOPS       NÃO           MORTE A BALA   
2      3  CIOPS       NÃO           MORTE A BALA   
3      4  CIOPS       NÃO           MORTE A BALA   
4      5  CIOPS       NÃO           MORTE A BALA   
..   ...    ...       ...                    ...   
562  563  CIOPS       NÃO     VEICULO LOCALIZADO   
563  564  CIOPS       NÃO     VEICULO LOCALIZADO   
564  565  CIOPS       NÃO     VEICULO LOCALIZADO   
565  566  CIOPS       NÃO     VEICULO LOCALIZADO   
566  567  CIOPS       NÃO     VEICULO LOCALIZADO   

                               HISTÓRICO DA OCORRÊNCIA  \
0    LOCAL: RUA CODO, JANGURUSSU. VÍTIMA: TIAGO S.P...   
1    LOCAL: AV. LESTE OESTE, PIRAMBU. VÍTIMA: RAFAE...   
2    LOCAL: RUA TAILANDIA, GENIBAÚ. VÍTIMA: ISRAEL ...   
3    LOCAL: RUA DR JOAQUIM FROTA SAPIRANGA COITÉ. V...   
4    LOCAL: RUA CARNAUBAL, ALVARO WEYNE. VÍTIMA: DI...   
..                                                 ...   
562  LOCAL: RUA SABINO FILHO, 12, SIQUEIRA. VEÍCULO...   
563  LOCAL: RUA AUGUSTO JAIME BENEVIDES,  GUARARAPE...   
564  LOCAL: AV. DOUTOR THEGERGE, BARRA DO CEARÁ.  V...   
565  LOCAL: RUA PEDRO MELO, ANTÔNIO BEZERRA.  VEÍCU...   
566  LOCAL: RUA SOLON PINHEIRO, FÁTIMA. VEÍCULO: FI...   

                                       LOCAL:  \
0                        RUA CODO, JANGURUSSU   
1                    AV. LESTE OESTE, PIRAMBU   
2                      RUA TAILANDIA, GENIBAU   
3        RUA DR JOAQUIM FROTA SAPIRANGA COITE   
4                 RUA CARNAUBAL, ALVARO WEYNE   
..                                        ...   
562            RUA SABINO FILHO, 12, SIQUEIRA   
563  RUA AUGUSTO JAIME BENEVIDES,  GUARARAPES   
564       AV. DOUTOR THEGERGE, BARRA DO CEARA   
565           RUA PEDRO MELO, ANTONIO BEZERRA   
566                RUA SOLON PINHEIRO, FATIMA   

                                   BAIRRO SUSPEITO:  \
0                              JANGURUSSU      nulo   
1                                 PIRAMBU      nulo   
2                                 GENIBAU      nulo   
3    RUA DR JOAQUIM FROTA SAPIRANGA COITE      nulo   
4                            ALVARO WEYNE      nulo   
..                                    ...       ...   
562                          12, SIQUEIRA      nulo   
563                            GUARARAPES      nulo   
564                        BARRA DO CEARA      nulo   
565                       ANTONIO BEZERRA      nulo   
566                                FATIMA      nulo   

                                      VEÍCULO:    VÍTIMA:  ...  \
0                                         nulo    TIAGO S  ...   
1                                         nulo  RAFAEL RS  ...   
2                                         nulo  ISRAEL RA  ...   
3                                         nulo     DAVI M  ...   
4                                         nulo    DIEGO T  ...   
..                                         ...        ...  ...   
562  CG 125 FAN KS, VERMELHA, 2012, OHX7263-CE       nulo  ...   
563                                    HB20S 1       nulo  ...   
564         CG150 FAN, PRETA, 2014, OST9220-CE       nulo  ...   
565     CHEVETTE, VERDE, 1984/1984, HUP7731-CE       nulo  ...   
566                             FIESTA SEDAN 1       nulo  ...   

    MATERIAL APREENDIDO: PLACA: VÍTIMAS LESIONADAS:         SUSPEITOS: HORA  \
0                   nulo   nulo                nulo  NÃO IDENTIFICADOS   10   
1                   nulo   nulo                nulo  NÃO IDENTIFICADOS   11   
2                   nulo   nulo                nulo  NÃO IDENTIFICADOS   13   
3                   nulo   nulo                nulo  NÃO IDENTIFICADOS   15   
4                   nulo   nulo                nulo  NÃO IDENTIFICADOS   17   
..                   ...    ...                 ...                ...  ...   
562                 nulo   nulo                nulo               nulo   13   
563      

Filtra as features para usar apenas latitude e longitude.
Transforma as coordenadas para radianos.
Usa a distância harvesiana.

In [183]:
coordenadas = data[['LATITUDE', 'LONGITUDE']]
coordenadas = coordenadas.applymap(lambda x: radians(x))
distancias = haversine_distances(coordenadas.values, coordenadas.values) * 6371000/1000

Cria o modelo de DBSCAN.

In [184]:
dbscan = DBSCAN(eps=1, min_samples=3, metric='precomputed')

Treina o modelo de DBSCAN com as distâncias

In [185]:
labels = dbscan.fit_predict(distancias)
len(set(dbscan.labels_)) - 1

11

In [186]:
labels

array([ 0,  1,  1,  2,  1,  1,  1,  1,  0,  1,  1,  1,  1,  3,  1,  1, -1,
        1,  1,  8,  1,  1,  1,  0,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
        1,  1,  1,  1,  1,  0,  1,  1,  1,  1,  1,  1,  1,  1,  0,  1,  0,
        1,  0,  4,  1,  1,  1,  1,  0,  0,  1,  0,  1,  2,  5,  1,  1,  1,
        0, -1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  2,  1,  1,  1,  1,  1,
        1,  1,  1,  6,  1,  0,  1,  0,  1,  1,  0,  1,  1,  2,  1,  0,  1,
        1,  0,  1,  1,  1,  1,  1,  0,  1,  2,  1,  1,  1,  1,  1,  1,  0,
        0,  8,  1,  0,  1,  1,  0,  1,  1,  0,  1,  1,  1,  2,  1,  1,  1,
        1,  7,  0,  1,  1,  1,  1,  1,  1,  1,  0,  1,  1,  1,  1,  2,  0,
        0,  0, -1,  0,  1,  1,  1,  1,  8,  1,  1,  1,  1,  1,  1,  1,  1,
       -1,  1,  1,  1,  6,  1,  1,  1,  1,  1,  5,  0,  1,  1,  1,  1,  1,
       -1, -1,  1,  1,  1,  2,  0,  1,  1,  0,  1,  9,  1,  1,  1,  1,  0,
        1,  1,  0,  0,  1,  1,  1,  1,  1,  1,  1,  0,  2,  1,  1,  1,  0,
        1,  0,  1,  1,  1

Cria o mapa

In [187]:
center_lat, center_lon = coordenadas.mean()
crime_map = folium.Map(location=[center_lat, center_lon], zoom_start=12)

Plota os pontos no mapa.
Cada ponto aplisenta a label do cluster se for clicado.

In [188]:
for index, row in data.iterrows():
    lat, lon = row['LATITUDE'], row['LONGITUDE']
    label = f"Cluster: {labels[index]}"
    folium.CircleMarker(location=[lat, lon], popup=label, radius=5, ill=True, fill_color='blue').add_to(crime_map)

In [189]:
crime_map

Cria e treina um modelo de kmeans com 11 clusters

In [190]:
kmeans = KMeans(n_clusters=11, random_state=42)
kmeans.fit(coordenadas)

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


KMeans(n_clusters=11, random_state=42)

In [191]:
labels = kmeans.labels_
len(set(kmeans.labels_))

11

In [192]:
labels

array([ 0,  1,  4,  3,  1,  4, 10,  1,  8,  1,  4,  4,  1,  9, 10,  4,  3,
       10,  3, 10,  5,  5,  3,  0,  4,  5,  1, 10,  4,  9,  4,  4,  2,  4,
        7,  1,  4,  1,  5,  0,  5, 10,  4,  1,  1, 10,  4,  4,  8,  4,  0,
        1,  8,  2,  1,  7,  4,  8,  0,  0,  3,  8,  2,  3,  8,  1, 10,  9,
        0,  2, 10,  1,  1,  2,  1,  1,  7,  8,  7,  3,  7,  1,  1,  1,  5,
        9,  7,  3,  2, 10,  8,  1,  0,  8, 10,  8,  7,  7,  3,  5,  0,  4,
        7,  8,  7,  1,  7,  4,  1,  0,  5,  3, 10,  7,  9, 10,  7,  7,  8,
        8,  9,  1,  0,  4,  9,  0,  7,  5,  0,  1,  1,  1,  3, 10,  7,  1,
        2,  3,  8,  9, 10,  9,  7,  4,  9,  1,  0,  7,  7,  7,  9,  3,  0,
        0,  0,  3,  8,  5,  2, 10,  1, 10,  1, 10,  5,  2,  7,  1,  9, 10,
        7,  1,  1,  4,  2,  7,  2, 10,  1,  7,  8,  8,  9, 10,  9,  4,  9,
        3,  0,  7, 10,  1,  3,  0,  4,  1,  0,  4,  0,  8,  7,  1,  4,  0,
        1,  4,  8,  8,  4, 10,  1, 10,  3,  4,  7,  8,  3,  1,  2,  9,  8,
        4,  8, 10,  4,  1

Plota os pontos no mapa

In [193]:
for index, row in data.iterrows():
    lat, lon = row['LATITUDE'], row['LONGITUDE']
    label = f"Cluster: {labels[index]}"
    folium.CircleMarker(location=[lat, lon], popup=label, radius=5, ill=True, fill_color='blue').add_to(crime_map)

In [194]:
crime_map

Cria e treina um modelo de clusterização hieráquica

In [195]:
Aclustering = AgglomerativeClustering(n_clusters=11)

In [196]:
Aclustering.fit(coordenadas)

AgglomerativeClustering(n_clusters=11)

In [197]:
labels = Aclustering.labels_
len(set(Aclustering.labels_))

11

In [198]:
labels

array([ 1,  4,  8, 10,  3,  3,  7,  3,  1,  3,  3,  8,  4,  7,  7,  8,  2,
        4,  6,  7,  2,  2,  6,  1,  3,  7,  3,  7,  8,  4,  8,  4,  0,  8,
        0,  3,  8,  4,  2,  1,  2,  7,  3,  4,  3,  6,  8,  8,  1,  3,  1,
        4,  1,  9,  3,  8,  8,  9,  1,  1,  6,  1,  0, 10,  6,  3,  7,  4,
        1,  0,  7,  3,  4,  0,  3,  4,  0,  9,  0, 10,  8,  4,  3,  3,  2,
        8,  0,  6,  9,  7,  1,  4,  1,  9,  7,  1,  0,  0, 10,  2,  1,  3,
        8,  1,  0,  3,  0,  8,  4,  1,  7, 10,  7,  8,  4,  4,  0,  8,  6,
        1,  7,  3,  1,  3,  4,  1,  0,  2,  1,  4,  4,  3, 10,  7,  8,  4,
        0,  2,  1,  9,  7,  4,  0,  3,  4,  3,  1,  0,  8,  0,  8, 10,  1,
        1,  1, 10,  1,  2,  9,  7,  4,  7,  4,  4,  2,  0,  8,  4,  4,  7,
        0,  4,  3,  8,  9,  8,  0,  7,  3,  8,  6,  6,  4,  7,  4,  3,  9,
       10,  1,  8,  4,  3, 10,  1,  3,  3,  1,  3,  1,  9,  8,  4,  8,  1,
        3,  3,  1,  1,  3,  7,  4,  7,  6,  8,  0,  1, 10,  3,  0,  9,  1,
        3,  1,  4,  3,  3

Plota os pontos no mapa

In [199]:
for index, row in data.iterrows():
    lat, lon = row['LATITUDE'], row['LONGITUDE']
    label = f"Cluster: {labels[index]}"
    folium.CircleMarker(location=[lat, lon], popup=label, radius=5, ill=True, fill_color='blue').add_to(crime_map)

In [200]:
crime_map

Em DBSCANS, a maioria dos pontos ficaram no cluster 1, o que não acontece no kmeans e hieráquico, eles distribuíram mais os pontos.